In [8]:
# Dependencies
# The dateparser library will be used to parser the date-time in local timezone
# pip install dateparser
# The gmaps and geopy libraries will be used to get the laitudes and longitudes of the accident location
# pip install gmaps
# pip install geopy
# The suntime library will be used to find the sun rise and sunset timings by the geo location
# pip install suntime
import pytz
import datetime as dt
from datetime import datetime
import dateparser
import gmaps
import numpy as np
import pandas as pd
import requests
import time
from pprint import pprint
from geopy.geocoders import Nominatim
from geopy import geocoders 
from scipy.stats import linregress
from matplotlib import pyplot as plt
import matplotlib.dates as mdates
from suntime import Sun, SunTimeException
import os
import json
import urllib.request


In [9]:
# Pull the accident data of a day in CSV format into a dataFrame
accident_data_to_load = "../Resources/US_Accidents_May19.csv"
accidents_data_df = pd.read_csv(accident_data_to_load)

# Visualize
accidents_data_df = accidents_data_df.reset_index()
accidents_data_df.set_index('ID', inplace=True)
accidents_data_df.head()


index State  Severity   Start_Time      End_Time  Start_Lat  Start_Lng  \
ID                                                                            
A-1      0    OH         3  2/8/16 5:46  2/8/16 11:00  39.865147 -84.058723   
A-2      1    OH         2  2/8/16 6:07   2/8/16 6:37  39.928059 -82.831184   
A-3      2    OH         2  2/8/16 6:49   2/8/16 7:19  39.063148 -84.032608   
A-4      3    OH         3  2/8/16 7:23   2/8/16 7:53  39.747753 -84.205582   
A-5      4    OH         2  2/8/16 7:39   2/8/16 8:09  39.627781 -84.188354   

     Distance(mi)                                        Description  Number  \
ID                                                                             
A-1          0.01  Right lane blocked due to accident on I-70 Eas...     NaN   
A-2          0.01  Accident on Brice Rd at Tussing Rd. Expect del...  2584.0   
A-3          0.01  Accident on OH-32 State Route 32 Westbound at ...     NaN   
A-4          0.01  Accident on I-75 Southbound at Exits 52 52B US...     NaN   
A-5          0.01  Accident on McEwen Rd at OH-725 Miamisburg Cen...     NaN   

             ...           Pressure(in) Visibility(mi) Wind_Direction  \
ID           ...                                                        
A-1          ...                  29.68           10.0           Calm   
A-2          ...                  29.65           10.0           Calm   
A-3          ...                  29.67           10.0             SW   
A-4          ...                  29.64            9.0             SW   
A-5          ...                  29.65            6.0             SW   

    Wind_Speed(mph) Precipitation(in) Weather_Condition Traffic_Signal  \
ID                                                                       
A-1             NaN              0.02        Light Rain          False   
A-2             NaN              0.00        Light Rain          False   
A-3             3.5               NaN          Overcast           True   
A-4             4.6               NaN     Mostly Cloudy          False   
A-5             3.5               NaN     Mostly Cloudy           True   

    Sunrise_Sunset Civil_Twilight  Astronomical_Twilight  
ID                                                        
A-1          Night          Night                  Night  
A-2          Night          Night                    Day  
A-3          Night          Night                    Day  
A-4          Night            Day                    Day  
A-5            Day            Day                    Day  

[5 rows x 32 columns]

In [10]:
# Check out all columns
list(accidents_data_df.columns) 

['index',
 'State',
 'Severity',
 'Start_Time',
 'End_Time',
 'Start_Lat',
 'Start_Lng',
 'Distance(mi)',
 'Description',
 'Number',
 'Street',
 'Side',
 'City',
 'County',
 'Zipcode',
 'Country',
 'Timezone',
 'Airport_Code',
 'Weather_Timestamp',
 'Temperature(F)',
 'Wind_Chill(F)',
 'Humidity(%)',
 'Pressure(in)',
 'Visibility(mi)',
 'Wind_Direction',
 'Wind_Speed(mph)',
 'Precipitation(in)',
 'Weather_Condition',
 'Traffic_Signal',
 'Sunrise_Sunset',
 'Civil_Twilight',
 'Astronomical_Twilight']

In [27]:
# Use the street column data to identify the freeways only for this project
accidents_data_df['hwy'] = accidents_data_df['Street'].str.split("-", n = 1, expand = True)[1].str.contains("E|W|N|S")== True
accidents_data_hwy_df = accidents_data_df.loc[accidents_data_df['hwy'] == True]
accidents_data_hwy_df.head()

index State  Severity   Start_Time      End_Time  Start_Lat  Start_Lng  \
ID                                                                             
A-1       0    OH         3  2/8/16 5:46  2/8/16 11:00  39.865147 -84.058723   
A-4       3    OH         3  2/8/16 7:23   2/8/16 7:53  39.747753 -84.205582   
A-12     11    OH         3  2/8/16 8:21   2/8/16 8:51  39.932709 -82.830910   
A-50     49    OH         3  2/9/16 6:41   2/9/16 7:11  39.773193 -84.187454   
A-59     58    OH         2  2/9/16 7:42   2/9/16 8:12  39.754520 -84.159279   

      Distance(mi)                                        Description  Number  \
ID                                                                              
A-1           0.01  Right lane blocked due to accident on I-70 Eas...     NaN   
A-4           0.01  Accident on I-75 Southbound at Exits 52 52B US...     NaN   
A-12          0.01  One lane blocked due to accident on I-70 Westb...     NaN   
A-50          0.01  Accident on I-75 Northbound at Exits 54A 54B O...     NaN   
A-59          0.01  Accident on US-35 Eastbound at Steve Whalen Bl...     NaN   

      ...  Visibility(mi) Wind_Direction Wind_Speed(mph) Precipitation(in)  \
ID    ...                                                                    
A-1   ...            10.0           Calm             NaN              0.02   
A-4   ...             9.0             SW             4.6               NaN   
A-12  ...             3.0            SSW             4.6              0.02   
A-50  ...             4.0             SW            11.5               NaN   
A-59  ...             1.2             SW             9.2              0.00   

     Weather_Condition Traffic_Signal Sunrise_Sunset Civil_Twilight  \
ID                                                                    
A-1         Light Rain          False          Night          Night   
A-4      Mostly Cloudy          False          Night            Day   
A-12        Light Rain          False            Day            Day   
A-50        Light Snow          False          Night          Night   
A-59        Light Snow          False            Day            Day   

     Astronomical_Twilight   hwy  
ID                                
A-1                  Night  True  
A-4                    Day  True  
A-12                   Day  True  
A-50                   Day  True  
A-59                   Day  True  

[5 rows x 33 columns]

In [23]:
# Output File (CSV)
os.makedirs(os.path.join('../output_data'),exist_ok=True)
output_data_file = os.path.join("../output_data","accidents_data_hwy_df.csv")
accidents_data_hwy_df.to_csv(output_data_file)

In [28]:
accident_data_hwy_to_load = "../Resources/accidents_data_hwy_df.csv"
accidents_hwy_df = pd.read_csv(accident_data_hwy_to_load, low_memory=False)

# Visualize
accidents_hwy_df = accidents_hwy_west_df.reset_index()
accidents_hwy_df.set_index('ID', inplace=True)
accidents_hwy_df.head()

level_0  index State  Severity   Start_Time      End_Time  Start_Lat  \
ID                                                                           
A-1         0      0    OH         3  2/8/16 5:46  2/8/16 11:00  39.865147   
A-12        1     11    OH         3  2/8/16 8:21   2/8/16 8:51  39.932709   
A-59        2     58    OH         2  2/9/16 7:42   2/9/16 8:12  39.754520   
A-60        3     59    OH         2  2/9/16 7:42   2/9/16 8:12  39.749916   
A-69        4     68    OH         3  2/9/16 8:35   2/9/16 9:05  41.424404   

      Start_Lng  Distance(mi)  \
ID                              
A-1  -84.058723          0.01   
A-12 -82.830910          0.01   
A-59 -84.159279          0.01   
A-60 -84.139359          0.01   
A-69 -81.578674          0.01   

                                            Description  ...   Visibility(mi)  \
ID                                                       ...                    
A-1   Right lane blocked due to accident on I-70 Eas...  ...             10.0   
A-12  One lane blocked due to accident on I-70 Westb...  ...              3.0   
A-59  Accident on US-35 Eastbound at Steve Whalen Bl...  ...              1.2   
A-60  Accident on US-35 Eastbound at Smithville Rd. ...  ...              1.2   
A-69  Accident on I-480 Eastbound at Exit 23 OH-14 B...  ...             10.0   

     Wind_Direction Wind_Speed(mph) Precipitation(in) Weather_Condition  \
ID                                                                        
A-1            Calm             NaN              0.02        Light Rain   
A-12            SSW             4.6              0.02        Light Rain   
A-59             SW             9.2              0.00        Light Snow   
A-60             SW             9.2              0.00        Light Snow   
A-69            WSW            12.7               NaN          Overcast   

     Traffic_Signal Sunrise_Sunset Civil_Twilight Astronomical_Twilight   hwy  
ID                                                                             
A-1           False          Night          Night                 Night  True  
A-12          False            Day            Day                   Day  True  
A-59          False            Day            Day                   Day  True  
A-60          False            Day            Day                   Day  True  
A-69          False            Day            Day                   Day  True  

[5 rows x 34 columns]

In [29]:
# Fetch all WestBound accidents
accidents_data_hwy_westbound_df = accidents_hwy_df.loc[accidents_hwy_df['Description'].str.contains("Westbound")]
# Fetch all EastBound accidents
accidents_data_hwy_eastbound_df = accidents_hwy_df.loc[accidents_hwy_df['Description'].str.contains("Eastbound")]
# Fetch all NorthBound accidents
accidents_data_hwy_northbound_df = accidents_hwy_df.loc[accidents_hwy_df['Description'].str.contains("Northbound")]
# Fetch all SouthBound accidents
accidents_data_hwy_southbound_df = accidents_hwy_df.loc[accidents_hwy_df['Description'].str.contains("Southbound")]
# Output File (CSV)
os.makedirs(os.path.join('../output_data'),exist_ok=True)
output_data_file = os.path.join("../output_data","accidents_data_hwy_westbound.csv")
accidents_data_hwy_westbound_df.to_csv(output_data_file)
output_data_file = os.path.join("../output_data","accidents_data_hwy_eastbound.csv")
accidents_data_hwy_eastbound_df.to_csv(output_data_file)
output_data_file = os.path.join("../output_data","accidents_data_hwy_northbound.csv")
accidents_data_hwy_northbound_df.to_csv(output_data_file)
output_data_file = os.path.join("../output_data","accidents_data_hwy_southbound.csv")
accidents_data_hwy_southbound_df.to_csv(output_data_file)
accidents_data_hwy_southbound_df.head()

In [183]:
accidents_data_hwy_westbound_df = accidents_hwy_west_df.loc[accidents_hwy_west_df['Direction_West'] == True]
accidents_data_hwy_westbound_df.head()

level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  Wind_Direction  \
ID                                                        ...                   
A-12   One lane blocked due to accident on I-70 Westb...  ...             SSW   
A-85   Left lane blocked due to accident on I-76 West...  ...             WNW   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...             SSW   
A-143  Lane blocked due to accident on I-670 Westboun...  ...              SE   
A-144  Left lane closed due to accident on I-70 Westb...  ...             SSE   

      Wind_Speed(mph) Precipitation(in)       Weather_Condition  \
ID                                                                
A-12              4.6              0.02              Light Rain   
A-85             10.4              0.00              Light Snow   
A-100             4.6               NaN        Scattered Clouds   
A-143             5.8              0.00  Light Freezing Drizzle   
A-144             8.1               NaN              Light Snow   

      Traffic_Signal Sunrise_Sunset Civil_Twilight Astronomical_Twilight  \
ID                                                                         
A-12           False            Day            Day                   Day   
A-85           False            Day            Day                   Day   
A-100          False            Day            Day                   Day   
A-143          False          Night          Night                 Night   
A-144          False          Night          Night                   Day   

        hwy Direction_West  
ID                          
A-12   True           True  
A-85   True           True  
A-100  True           True  
A-143  True           True  
A-144  True           True  

[5 rows x 35 columns]

In [184]:
len(accidents_data_hwy_westbound_df)


52726

In [185]:
accidents_data_hwy_westbound_df['Accident_Date'] = accidents_data_hwy_westbound_df['Start_Time'].str.split(" ", n = 1, expand = True)[0]
accidents_data_hwy_westbound_df.head()

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  \
ID                                                        ...   
A-12   One lane blocked due to accident on I-70 Westb...  ...   
A-85   Left lane blocked due to accident on I-76 West...  ...   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...   
A-143  Lane blocked due to accident on I-670 Westboun...  ...   
A-144  Left lane closed due to accident on I-70 Westb...  ...   

       Wind_Speed(mph) Precipitation(in)       Weather_Condition  \
ID                                                                 
A-12               4.6              0.02              Light Rain   
A-85              10.4              0.00              Light Snow   
A-100              4.6               NaN        Scattered Clouds   
A-143              5.8              0.00  Light Freezing Drizzle   
A-144              8.1               NaN              Light Snow   

      Traffic_Signal Sunrise_Sunset Civil_Twilight Astronomical_Twilight  \
ID                                                                         
A-12           False            Day            Day                   Day   
A-85           False            Day            Day                   Day   
A-100          False            Day            Day                   Day   
A-143          False          Night          Night                 Night   
A-144          False          Night          Night                   Day   

        hwy Direction_West Accident_Date  
ID                                        
A-12   True           True        2/8/16  
A-85   True           True       2/10/16  
A-100  True           True       2/11/16  
A-143  True           True       2/15/16  
A-144  True           True       2/15/16  

[5 rows x 36 columns]

In [186]:
accidents_data_hwy_westbound_df['Accident_Date'] = pd.to_datetime(accidents_data_hwy_westbound_df['Accident_Date'])
accidents_data_hwy_westbound_df['Accident_Date_No_Time'] = accidents_data_hwy_westbound_df['Accident_Date'].dt.date
accidents_data_hwy_westbound_df.head()

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  \
ID                                                        ...   
A-12   One lane blocked due to accident on I-70 Westb...  ...   
A-85   Left lane blocked due to accident on I-76 West...  ...   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...   
A-143  Lane blocked due to accident on I-670 Westboun...  ...   
A-144  Left lane closed due to accident on I-70 Westb...  ...   

       Precipitation(in)       Weather_Condition Traffic_Signal  \
ID                                                                
A-12                0.02              Light Rain          False   
A-85                0.00              Light Snow          False   
A-100                NaN        Scattered Clouds          False   
A-143               0.00  Light Freezing Drizzle          False   
A-144                NaN              Light Snow          False   

      Sunrise_Sunset Civil_Twilight Astronomical_Twilight   hwy  \
ID                                                                
A-12             Day            Day                   Day  True   
A-85             Day            Day                   Day  True   
A-100            Day            Day                   Day  True   
A-143          Night          Night                 Night  True   
A-144          Night          Night                   Day  True   

      Direction_West Accident_Date Accident_Date_No_Time  
ID                                                        
A-12            True    2016-02-08            2016-02-08  
A-85            True    2016-02-10            2016-02-10  
A-100           True    2016-02-11            2016-02-11  
A-143           True    2016-02-15            2016-02-15  
A-144           True    2016-02-15            2016-02-15  

[5 rows x 37 columns]

In [187]:
len(accidents_data_hwy_westbound_df)

52726

In [188]:

sunset_time = []
count = 0
for lat, lng, date in zip(accidents_data_hwy_westbound_df.loc[:, 'Start_Lat'], accidents_data_hwy_westbound_df.loc[:, 'Start_Lng'],accidents_data_hwy_westbound_df.loc[:, 'Accident_Date_No_Time']):
    #print(lat, lng, date)
    sun = Sun(lat, lng)
    sunset_time_pst = sun.get_local_sunset_time(date)
    #print(sunset_time)
    pst_dt = dateparser.parse(str(sunset_time_pst))
    utc_dt = pst_dt.astimezone(dt.timezone.utc)
    sunset_time_utc = utc_dt.strftime('%Y-%m-%d %H:%M')
    print(sunset_time_utc) 
    sunset_time.append(sunset_time_utc)
    count+=1
    
print(count)    

2016-02-08 22:59
2016-02-10 22:54
2016-02-11 23:08
2016-02-15 23:08
2016-02-15 23:08
2016-02-16 23:09
2016-02-17 23:06
2016-02-26 23:14
2016-03-03 23:32
2016-03-04 23:28
2016-03-10 23:34
2016-03-15 23:38
2016-03-16 23:40
2016-06-21 03:33
2016-06-21 03:34
2016-06-21 03:34
2016-06-21 03:33
2016-06-21 03:32
2016-06-21 03:33
2016-06-21 03:35
2016-06-21 03:31
2016-06-21 03:34
2016-06-21 03:35
2016-06-21 03:31
2016-06-22 03:34
2016-06-22 03:33
2016-06-22 03:34
2016-06-22 03:35
2016-06-22 03:35
2016-06-22 03:32
2016-06-22 03:35
2016-06-22 03:34
2016-06-22 03:33
2016-06-22 03:35
2016-06-22 03:34
2016-06-22 03:35
2016-06-23 03:35
2016-06-23 03:34
2016-06-23 03:35
2016-06-23 03:35
2016-06-23 03:32
2016-06-23 03:35
2016-06-23 03:32
2016-06-23 03:32
2016-06-23 03:35
2016-06-24 03:33
2016-06-24 03:35
2016-06-24 03:35
2016-06-24 03:35
2016-06-24 03:35
2016-06-24 03:35
2016-06-24 03:35
2016-06-24 03:34
2016-06-24 03:35
2016-06-24 03:32
2016-06-24 03:34
2016-06-24 03:34
2016-06-24 03:35
2016-06-24 03:

2016-12-09 00:48
2016-12-09 00:49
2016-12-09 00:41
2016-12-10 00:42
2016-12-10 00:51
2016-12-10 00:50
2016-12-10 00:49
2016-12-10 00:50
2016-12-10 00:48
2016-12-10 00:50
2016-12-10 00:47
2016-12-11 00:50
2016-12-12 00:51
2016-12-12 00:50
2016-12-12 00:50
2016-12-12 00:50
2016-12-12 00:50
2016-12-12 00:51
2016-12-12 00:49
2016-12-13 00:48
2016-12-13 00:48
2016-12-13 00:50
2016-12-13 00:50
2016-12-13 00:51
2016-12-13 00:44
2016-12-13 00:51
2016-12-14 00:51
2016-12-14 00:51
2016-12-14 00:50
2016-12-14 00:50
2016-12-14 00:49
2016-12-14 00:51
2016-12-14 00:45
2016-12-14 00:51
2016-12-14 00:51
2016-12-14 00:51
2016-12-14 00:50
2016-12-15 00:51
2016-12-15 00:52
2016-12-15 00:49
2016-12-15 00:50
2016-12-15 00:49
2016-12-15 00:51
2016-12-15 00:51
2016-12-15 00:45
2016-12-15 00:51
2016-12-15 00:46
2016-12-15 00:46
2016-12-15 00:51
2016-12-15 00:51
2016-12-15 00:47
2016-12-16 00:51
2016-12-16 00:52
2016-12-16 00:52
2016-12-16 00:48
2016-12-16 00:49
2016-12-16 00:51
2016-12-16 00:50
2016-12-16 00:

2016-10-20 01:24
2016-10-20 01:22
2016-10-20 01:23
2016-10-21 01:21
2016-10-21 01:22
2016-10-21 01:21
2016-10-21 01:22
2016-10-21 01:21
2016-10-21 01:21
2016-10-21 01:22
2016-10-21 01:23
2016-10-21 01:18
2016-10-21 01:20
2016-10-21 01:22
2016-10-21 01:21
2016-10-21 01:18
2016-10-21 01:22
2016-10-21 01:22
2016-10-21 01:22
2016-10-21 01:23
2016-10-21 01:20
2016-10-22 01:18
2016-10-22 01:22
2016-10-22 01:21
2016-10-22 01:17
2016-10-23 01:20
2016-10-23 01:19
2016-10-23 01:18
2016-10-23 01:20
2016-10-23 01:16
2016-10-23 01:15
2016-10-23 01:16
2016-10-24 01:19
2016-10-24 01:17
2016-10-24 01:18
2016-10-24 01:18
2016-10-24 01:17
2016-10-24 01:19
2016-10-24 01:19
2016-10-24 01:17
2016-10-24 01:17
2016-10-24 01:14
2016-10-24 01:17
2016-10-24 01:18
2016-10-24 01:17
2016-10-24 01:15
2016-10-24 01:19
2016-10-24 01:19
2016-10-24 01:19
2016-10-25 01:15
2016-10-25 01:17
2016-10-25 01:15
2016-10-25 01:17
2016-10-25 01:17
2016-10-25 01:15
2016-10-25 01:18
2016-10-25 01:17
2016-10-25 01:17
2016-10-25 01:

2016-11-27 00:45
2016-11-27 00:51
2016-11-27 00:49
2016-11-27 00:48
2016-11-28 00:51
2016-11-28 00:48
2016-11-28 00:49
2016-11-28 00:50
2016-11-28 00:51
2016-11-28 00:50
2016-11-28 00:48
2016-11-28 00:47
2016-11-28 00:48
2016-11-28 00:50
2016-11-28 00:48
2016-11-28 00:40
2016-11-28 00:50
2016-11-28 00:49
2016-11-28 00:49
2016-11-28 00:47
2016-11-28 00:51
2016-11-28 00:50
2016-11-28 00:50
2016-11-28 00:44
2016-11-28 00:44
2016-11-28 00:51
2016-11-29 00:44
2016-11-29 00:49
2016-11-29 00:49
2016-11-29 00:45
2016-11-29 00:50
2016-11-29 00:49
2016-11-29 00:48
2016-11-29 00:51
2016-11-29 00:50
2016-11-30 00:49
2016-11-30 00:50
2016-11-30 00:48
2016-11-30 00:44
2016-11-30 00:50
2016-11-30 00:47
2016-11-30 00:49
2016-11-30 00:50
2016-11-30 00:44
2016-11-30 00:50
2016-09-11 02:18
2016-09-12 02:21
2016-09-12 02:16
2016-09-12 02:19
2016-09-12 02:19
2016-09-12 02:19
2016-09-12 02:17
2016-09-12 02:17
2016-09-12 02:20
2016-09-12 02:16
2016-09-12 02:20
2016-09-12 02:18
2016-09-12 02:17
2016-09-12 02:

2016-10-14 01:30
2016-10-14 01:30
2016-10-14 01:31
2016-10-14 01:31
2016-10-14 01:27
2016-10-14 01:31
2016-10-14 01:31
2016-10-14 01:31
2016-10-14 01:32
2016-10-14 01:31
2016-10-15 01:30
2016-10-15 01:30
2016-10-15 01:29
2016-10-15 01:31
2016-10-15 01:30
2016-10-15 01:28
2016-10-15 01:31
2016-10-15 01:26
2016-10-15 01:30
2016-10-16 01:27
2016-10-16 01:28
2016-10-16 01:27
2016-10-16 01:22
2016-10-16 01:28
2016-10-16 01:28
2016-10-16 01:24
2016-10-16 01:27
2016-10-16 01:26
2016-10-16 01:28
2016-10-16 01:28
2016-10-16 01:28
2016-10-16 01:28
2016-10-16 01:27
2016-10-16 01:28
2016-10-16 01:27
2016-10-16 01:23
2016-10-16 01:29
2016-10-16 01:24
2016-10-16 01:23
2016-10-17 01:27
2016-10-17 01:25
2016-10-17 01:25
2016-10-17 01:27
2016-10-17 01:26
2016-10-17 01:27
2016-10-17 01:26
2016-10-17 01:26
2016-10-17 01:27
2016-10-17 01:26
2016-10-17 01:26
2016-10-18 01:26
2016-10-18 01:25
2016-10-18 01:26
2016-10-18 01:26
2016-10-18 01:26
2016-10-18 01:25
2016-10-18 01:25
2016-10-18 01:25
2016-10-18 01:

...

2018-07-04 00:34
2018-07-04 00:34
2018-07-04 00:27
2018-07-04 00:27
2018-07-04 00:29
2018-07-04 00:39
2018-07-04 00:36
2018-07-04 00:51
2018-07-04 00:52
2018-07-04 00:34
2018-07-04 00:41
2018-07-04 00:32
2018-07-04 01:59
2018-07-04 01:30
2018-07-04 01:33
2018-07-04 01:30
2018-07-04 01:38
2018-07-04 01:39
2018-07-04 01:05
2018-07-04 01:18
2018-07-04 01:07
2018-07-04 01:07
2018-07-04 01:20
2018-07-04 01:26
2018-07-04 02:29
2018-07-04 03:01
2018-07-04 02:35
2018-07-04 04:09
2018-07-04 03:34
2018-07-04 03:35
2018-07-04 03:33
2018-07-04 03:19
2018-07-04 03:04
2018-07-04 03:08
2018-07-04 03:00
2018-07-04 03:04
2018-07-04 03:05
2018-07-04 03:00
2018-07-04 03:05
2018-07-04 03:06
2018-07-05 00:58
2018-07-05 00:20
2018-07-05 00:36
2018-07-05 00:37
2018-07-05 00:37
2018-07-05 00:51
2018-07-05 00:30
2018-07-05 00:30
2018-07-05 00:32
2018-07-05 00:35
2018-07-05 01:01
2018-07-05 00:38
2018-07-05 00:40
2018-07-05 00:37
2018-07-05 00:37
2018-07-05 00:38
2018-07-05 00:38
2018-07-05 00:38
2018-07-05 01:

2018-07-11 00:23
2018-07-11 00:33
2018-07-11 00:43
2018-07-11 00:42
2018-07-11 00:48
2018-07-11 00:24
2018-07-11 00:33
2018-07-11 00:30
2018-07-11 00:27
2018-07-11 01:01
2018-07-11 00:39
2018-07-11 00:43
2018-07-11 01:14
2018-07-11 01:07
2018-07-11 01:14
2018-07-11 01:05
2018-07-11 00:57
2018-07-11 00:33
2018-07-11 00:33
2018-07-11 00:33
2018-07-11 00:33
2018-07-11 00:27
2018-07-11 00:26
2018-07-11 00:30
2018-07-11 00:32
2018-07-11 00:16
2018-07-11 00:16
2018-07-11 00:26
2018-07-11 00:16
2018-07-11 00:26
2018-07-11 00:50
2018-07-11 00:50
2018-07-11 00:37
2018-07-11 00:50
2018-07-11 00:38
2018-07-11 00:32
2018-07-11 00:31
2018-07-11 00:31
2018-07-11 00:48
2018-07-11 01:26
2018-07-11 01:59
2018-07-11 01:58
2018-07-11 01:58
2018-07-11 01:59
2018-07-11 01:58
2018-07-11 02:00
2018-07-11 02:00
2018-07-11 02:00
2018-07-11 02:00
2018-07-11 02:01
2018-07-11 01:29
2018-07-11 01:36
2018-07-11 01:39
2018-07-11 01:48
2018-07-11 01:09
2018-07-11 01:38
2018-07-11 01:16
2018-07-11 01:04
2018-07-11 01:

2018-07-17 01:23
2018-07-17 01:45
2018-07-17 01:35
2018-07-17 01:45
2018-07-17 00:55
2018-07-17 00:55
2018-07-17 00:55
2018-07-17 01:35
2018-07-17 01:03
2018-07-17 01:03
2018-07-17 01:03
2018-07-17 01:03
2018-07-17 01:02
2018-07-17 01:22
2018-07-17 00:59
2018-07-17 01:22
2018-07-17 02:26
2018-07-17 02:54
2018-07-17 02:57
2018-07-17 02:37
2018-07-17 04:01
2018-07-16 03:31
2018-07-17 03:30
2018-07-17 03:30
2018-07-17 03:29
2018-07-17 03:28
2018-07-17 03:30
2018-07-17 03:28
2018-07-17 03:30
2018-07-17 03:29
2018-07-17 03:30
2018-07-17 03:30
2018-07-17 03:27
2018-07-17 03:30
2018-07-17 03:28
2018-07-17 03:29
2018-07-17 03:30
2018-07-17 03:32
2018-07-17 03:17
2018-07-17 02:59
2018-07-17 02:59
2018-07-17 03:04
2018-07-17 03:01
2018-07-17 03:01
2018-07-17 03:00
2018-07-17 03:01
2018-07-17 02:56
2018-07-17 03:00
2018-07-17 03:03
2018-07-17 03:04
2018-07-17 03:05
2018-07-17 03:02
2018-07-17 03:01
2018-07-17 03:01
2018-07-17 03:04
2018-07-17 03:01
2018-07-17 03:04
2018-07-17 03:03
2018-07-18 01:

2018-07-23 01:38
2018-07-23 01:37
2018-07-23 01:20
2018-07-23 01:21
2018-07-23 01:32
2018-07-23 01:33
2018-07-23 01:32
2018-07-23 01:07
2018-07-23 01:34
2018-07-23 01:33
2018-07-23 01:30
2018-07-23 01:05
2018-07-23 01:05
2018-07-23 00:53
2018-07-23 01:22
2018-07-23 01:32
2018-07-23 01:32
2018-07-23 01:32
2018-07-23 00:48
2018-07-23 00:59
2018-07-23 00:54
2018-07-23 00:49
2018-07-23 00:57
2018-07-23 00:59
2018-07-23 00:59
2018-07-23 00:43
2018-07-23 02:21
2018-07-23 02:21
2018-07-23 02:21
2018-07-23 02:22
2018-07-23 02:21
2018-07-23 02:34
2018-07-23 03:22
2018-07-23 03:26
2018-07-23 03:26
2018-07-23 03:25
2018-07-23 03:25
2018-07-23 03:25
2018-07-23 03:24
2018-07-23 03:27
2018-07-23 03:26
2018-07-23 03:27
2018-07-23 03:26
2018-07-23 03:24
2018-07-23 03:26
2018-07-23 03:24
2018-07-23 03:09
2018-07-23 03:07
2018-07-23 03:00
2018-07-23 02:58
2018-07-23 02:58
2018-07-23 02:57
2018-07-23 02:56
2018-07-23 03:00
2018-07-23 02:57
2018-07-23 02:56
2018-07-23 02:58
2018-07-23 03:01
2018-07-23 02:

2018-07-28 00:19
2018-07-28 00:21
2018-07-28 00:29
2018-07-28 00:41
2018-07-28 00:41
2018-07-28 00:24
2018-07-28 00:35
2018-07-28 01:45
2018-07-28 01:47
2018-07-28 01:46
2018-07-28 01:06
2018-07-28 01:30
2018-07-28 01:01
2018-07-28 00:49
2018-07-28 00:54
2018-07-28 01:17
2018-07-28 01:17
2018-07-28 01:16
2018-07-27 03:23
2018-07-28 03:21
2018-07-28 03:22
2018-07-28 03:22
2018-07-28 03:22
2018-07-28 03:22
2018-07-28 03:20
2018-07-28 03:09
2018-07-27 02:56
2018-07-28 02:57
2018-07-28 02:55
2018-07-28 02:53
2018-07-28 02:50
2018-07-28 02:55
2018-07-28 02:54
2018-07-28 02:54
2018-07-28 02:50
2018-07-28 02:56
2018-07-28 02:50
2018-07-28 02:56
2018-07-29 00:38
2018-07-29 00:58
2018-07-29 00:24
2018-07-29 00:24
2018-07-29 00:20
2018-07-29 00:24
2018-07-29 00:20
2018-07-29 00:28
2018-07-29 00:52
2018-07-29 00:52
2018-07-29 00:29
2018-07-29 00:15
2018-07-29 00:15
2018-07-29 00:21
2018-07-29 00:22
2018-07-29 00:18
2018-07-29 00:20
2018-07-29 00:39
2018-07-29 00:40
2018-07-29 00:28
2018-07-29 00:

In [189]:
accidents_data_hwy_westbound_sunset_df = accidents_data_hwy_westbound_df.iloc[:count, :]
accidents_data_hwy_westbound_sunset_df.head()

level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  \
ID                                                        ...   
A-12   One lane blocked due to accident on I-70 Westb...  ...   
A-85   Left lane blocked due to accident on I-76 West...  ...   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...   
A-143  Lane blocked due to accident on I-670 Westboun...  ...   
A-144  Left lane closed due to accident on I-70 Westb...  ...   

       Precipitation(in)       Weather_Condition Traffic_Signal  \
ID                                                                
A-12                0.02              Light Rain          False   
A-85                0.00              Light Snow          False   
A-100                NaN        Scattered Clouds          False   
A-143               0.00  Light Freezing Drizzle          False   
A-144                NaN              Light Snow          False   

      Sunrise_Sunset Civil_Twilight Astronomical_Twilight   hwy  \
ID                                                                
A-12             Day            Day                   Day  True   
A-85             Day            Day                   Day  True   
A-100            Day            Day                   Day  True   
A-143          Night          Night                 Night  True   
A-144          Night          Night                   Day  True   

      Direction_West Accident_Date Accident_Date_No_Time  
ID                                                        
A-12            True    2016-02-08            2016-02-08  
A-85            True    2016-02-10            2016-02-10  
A-100           True    2016-02-11            2016-02-11  
A-143           True    2016-02-15            2016-02-15  
A-144           True    2016-02-15            2016-02-15  

[5 rows x 37 columns]

In [190]:
len(accidents_data_hwy_westbound_sunset_df)

52726

In [191]:
accidents_data_hwy_westbound_sunset_df['Sunset_Time_UTC'] = sunset_time
accidents_data_hwy_westbound_sunset_df.head()

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  \
ID                                                        ...   
A-12   One lane blocked due to accident on I-70 Westb...  ...   
A-85   Left lane blocked due to accident on I-76 West...  ...   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...   
A-143  Lane blocked due to accident on I-670 Westboun...  ...   
A-144  Left lane closed due to accident on I-70 Westb...  ...   

            Weather_Condition Traffic_Signal Sunrise_Sunset Civil_Twilight  \
ID                                                                           
A-12               Light Rain          False            Day            Day   
A-85               Light Snow          False            Day            Day   
A-100        Scattered Clouds          False            Day            Day   
A-143  Light Freezing Drizzle          False          Night          Night   
A-144              Light Snow          False          Night          Night   

      Astronomical_Twilight   hwy Direction_West Accident_Date  \
ID                                                               
A-12                    Day  True           True    2016-02-08   
A-85                    Day  True           True    2016-02-10   
A-100                   Day  True           True    2016-02-11   
A-143                 Night  True           True    2016-02-15   
A-144                   Day  True           True    2016-02-15   

      Accident_Date_No_Time   Sunset_Time_UTC  
ID                                             
A-12             2016-02-08  2016-02-08 22:59  
A-85             2016-02-10  2016-02-10 22:54  
A-100            2016-02-11  2016-02-11 23:08  
A-143            2016-02-15  2016-02-15 23:08  
A-144            2016-02-15  2016-02-15 23:08  

[5 rows x 38 columns]

In [192]:
del accidents_data_hwy_westbound_sunset_df['Accident_Date']
accidents_data_hwy_westbound_sunset_df.head()

level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  \
ID                                                        ...   
A-12   One lane blocked due to accident on I-70 Westb...  ...   
A-85   Left lane blocked due to accident on I-76 West...  ...   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...   
A-143  Lane blocked due to accident on I-670 Westboun...  ...   
A-144  Left lane closed due to accident on I-70 Westb...  ...   

       Precipitation(in)       Weather_Condition Traffic_Signal  \
ID                                                                
A-12                0.02              Light Rain          False   
A-85                0.00              Light Snow          False   
A-100                NaN        Scattered Clouds          False   
A-143               0.00  Light Freezing Drizzle          False   
A-144                NaN              Light Snow          False   

      Sunrise_Sunset Civil_Twilight Astronomical_Twilight   hwy  \
ID                                                                
A-12             Day            Day                   Day  True   
A-85             Day            Day                   Day  True   
A-100            Day            Day                   Day  True   
A-143          Night          Night                 Night  True   
A-144          Night          Night                   Day  True   

      Direction_West Accident_Date_No_Time   Sunset_Time_UTC  
ID                                                            
A-12            True            2016-02-08  2016-02-08 22:59  
A-85            True            2016-02-10  2016-02-10 22:54  
A-100           True            2016-02-11  2016-02-11 23:08  
A-143           True            2016-02-15  2016-02-15 23:08  
A-144           True            2016-02-15  2016-02-15 23:08  

[5 rows x 37 columns]

In [193]:
accidents_data_hwy_westbound_sunset_df = accidents_data_hwy_westbound_sunset_df.rename({'Accident_Date_No_Time':'Accident_Date'}, axis=1)
accidents_data_hwy_westbound_sunset_df.head()

level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  \
ID                                                        ...   
A-12   One lane blocked due to accident on I-70 Westb...  ...   
A-85   Left lane blocked due to accident on I-76 West...  ...   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...   
A-143  Lane blocked due to accident on I-670 Westboun...  ...   
A-144  Left lane closed due to accident on I-70 Westb...  ...   

       Precipitation(in)       Weather_Condition Traffic_Signal  \
ID                                                                
A-12                0.02              Light Rain          False   
A-85                0.00              Light Snow          False   
A-100                NaN        Scattered Clouds          False   
A-143               0.00  Light Freezing Drizzle          False   
A-144                NaN              Light Snow          False   

      Sunrise_Sunset Civil_Twilight Astronomical_Twilight   hwy  \
ID                                                                
A-12             Day            Day                   Day  True   
A-85             Day            Day                   Day  True   
A-100            Day            Day                   Day  True   
A-143          Night          Night                 Night  True   
A-144          Night          Night                   Day  True   

      Direction_West Accident_Date   Sunset_Time_UTC  
ID                                                    
A-12            True    2016-02-08  2016-02-08 22:59  
A-85            True    2016-02-10  2016-02-10 22:54  
A-100           True    2016-02-11  2016-02-11 23:08  
A-143           True    2016-02-15  2016-02-15 23:08  
A-144           True    2016-02-15  2016-02-15 23:08  

[5 rows x 37 columns]

In [194]:
accidents_data_hwy_westbound_sunset_df['Accident_Time'] = accidents_data_hwy_westbound_sunset_df['Start_Time'].str.split(" ", n = 1, expand = True)[1]
accidents_data_hwy_westbound_sunset_df.head()

level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  \
ID                                                        ...   
A-12   One lane blocked due to accident on I-70 Westb...  ...   
A-85   Left lane blocked due to accident on I-76 West...  ...   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...   
A-143  Lane blocked due to accident on I-670 Westboun...  ...   
A-144  Left lane closed due to accident on I-70 Westb...  ...   

            Weather_Condition Traffic_Signal Sunrise_Sunset Civil_Twilight  \
ID                                                                           
A-12               Light Rain          False            Day            Day   
A-85               Light Snow          False            Day            Day   
A-100        Scattered Clouds          False            Day            Day   
A-143  Light Freezing Drizzle          False          Night          Night   
A-144              Light Snow          False          Night          Night   

      Astronomical_Twilight   hwy Direction_West Accident_Date  \
ID                                                               
A-12                    Day  True           True    2016-02-08   
A-85                    Day  True           True    2016-02-10   
A-100                   Day  True           True    2016-02-11   
A-143                 Night  True           True    2016-02-15   
A-144                   Day  True           True    2016-02-15   

        Sunset_Time_UTC Accident_Time  
ID                                     
A-12   2016-02-08 22:59          8:21  
A-85   2016-02-10 22:54         17:10  
A-100  2016-02-11 23:08          8:13  
A-143  2016-02-15 23:08          5:42  
A-144  2016-02-15 23:08          6:36  

[5 rows x 38 columns]

In [195]:
pytz.all_timezones

['Africa/Abidjan',
 'Africa/Accra',
 'Africa/Addis_Ababa',
 'Africa/Algiers',
 'Africa/Asmara',
 'Africa/Asmera',
 'Africa/Bamako',
 'Africa/Bangui',
 'Africa/Banjul',
 'Africa/Bissau',
 'Africa/Blantyre',
 'Africa/Brazzaville',
 'Africa/Bujumbura',
 'Africa/Cairo',
 'Africa/Casablanca',
 'Africa/Ceuta',
 'Africa/Conakry',
 'Africa/Dakar',
 'Africa/Dar_es_Salaam',
 'Africa/Djibouti',
 'Africa/Douala',
 'Africa/El_Aaiun',
 'Africa/Freetown',
 'Africa/Gaborone',
 'Africa/Harare',
 'Africa/Johannesburg',
 'Africa/Juba',
 'Africa/Kampala',
 'Africa/Khartoum',
 'Africa/Kigali',
 'Africa/Kinshasa',
 'Africa/Lagos',
 'Africa/Libreville',
 'Africa/Lome',
 'Africa/Luanda',
 'Africa/Lubumbashi',
 'Africa/Lusaka',
 'Africa/Malabo',
 'Africa/Maputo',
 'Africa/Maseru',
 'Africa/Mbabane',
 'Africa/Mogadishu',
 'Africa/Monrovia',
 'Africa/Nairobi',
 'Africa/Ndjamena',
 'Africa/Niamey',
 'Africa/Nouakchott',
 'Africa/Ouagadougou',
 'Africa/Porto-Novo',
 'Africa/Sao_Tome',
 'Africa/Timbuktu',
 'Africa/

In [198]:
sunset_time_local = []

for date, time, timezone in zip(accidents_data_hwy_westbound_sunset_df.loc[:, 'Accident_Date'], accidents_data_hwy_westbound_sunset_df.loc[:, 'Sunset_Time_UTC'], accidents_data_hwy_westbound_sunset_df.loc[:, 'Timezone']):
    #print(timezone)  
    est = pytz.timezone('US/Eastern')
    pst = pytz.timezone('US/Pacific')
    mst = pytz.timezone('US/Mountain')
    cst = pytz.timezone('US/Central')
    ast = pytz.timezone('US/Alaska')
    hst = pytz.timezone('US/Hawaii')
    arst = pytz.timezone('US/Arizona')
    alst = pytz.timezone('US/Aleutian')
    eist = pytz.timezone('US/East-Indiana')
    isst = pytz.timezone('US/Indiana-Starke')
    mist = pytz.timezone('US/Michigan')
    sst = pytz.timezone('US/Samoa')
    #utc = pytz.utc
    fmt = '%Y-%m-%d %H:%M'
    sunset_time_no_date = time.split(' ')[1]
    #print(sunset_time_no_date)
    utc_time = datetime(int(str(date).split('-')[0]), int(str(date).split('-')[1]), int(str(date).split('-')[2]), int(str(sunset_time_no_date).split(':')[0]), int(str(sunset_time_no_date).split(':')[1]), tzinfo=utc)
    
    #print(utc_time)
    if (timezone == 'US/Eastern'): 
        sunset_time_local.append(utc_time.astimezone(est).strftime(fmt))
    elif (timezone == 'US/Pacific'):        
        sunset_time_local.append(utc_time.astimezone(pst).strftime(fmt))
    elif (timezone == 'US/Mountain'):        
        sunset_time_local.append(utc_time.astimezone(mst).strftime(fmt))
    elif (timezone == 'US/Central'):        
        sunset_time_local.append(utc_time.astimezone(cst).strftime(fmt))
    elif (timezone == 'US/Alaska'):      
        sunset_time_local.append(utc_time.astimezone(ast).strftime(fmt))
    elif (timezone == 'US/Hawaii'):        
        sunset_time_local.append(utc_time.astimezone(hst).strftime(fmt))
    elif (timezone == 'US/Arizona'):        
        sunset_time_local.append(utc_time.astimezone(arst).strftime(fmt))
    elif (timezone == 'US/Aleutian'):        
        sunset_time_local.append(utc_time.astimezone(alst).strftime(fmt))
    elif (timezone == 'US/East-Indiana'):        
        sunset_time_local.append(utc_time.astimezone(eist).strftime(fmt))    
    elif (timezone == 'US/Indiana-Starke'):        
        sunset_time_local.append(utc_time.astimezone(isst).strftime(fmt))
    elif (timezone == 'US/Michigan'):        
        sunset_time_local.append(utc_time.astimezone(mist).strftime(fmt))
    elif (timezone == 'US/Samoa'):        
        sunset_time_local.append(utc_time.astimezone(sst).strftime(fmt))
    else:
        sunset_time_local.append(utc_time.astimezone(pst).strftime(fmt)) 
    
print(sunset_time_local)

['2016-02-08 17:59', '2016-02-10 17:54', '2016-02-11 18:08', '2016-02-15 18:08', '2016-02-15 18:08', '2016-02-16 18:09', '2016-02-17 18:06', '2016-02-26 18:14', '2016-03-03 18:32', '2016-03-04 18:28', '2016-03-10 18:34', '2016-03-15 19:38', '2016-03-16 19:40', '2016-06-20 20:33', '2016-06-20 20:34', '2016-06-20 20:34', '2016-06-20 20:33', '2016-06-20 20:32', '2016-06-20 20:33', '2016-06-20 20:35', '2016-06-20 20:31', '2016-06-20 20:34', '2016-06-20 20:35', '2016-06-20 20:31', '2016-06-21 20:34', '2016-06-21 20:33', '2016-06-21 20:34', '2016-06-21 20:35', '2016-06-21 20:35', '2016-06-21 20:32', '2016-06-21 20:35', '2016-06-21 20:34', '2016-06-21 20:33', '2016-06-21 20:35', '2016-06-21 20:34', '2016-06-21 20:35', '2016-06-22 20:35', '2016-06-22 20:34', '2016-06-22 20:35', '2016-06-22 20:35', '2016-06-22 20:32', '2016-06-22 20:35', '2016-06-22 20:32', '2016-06-22 20:32', '2016-06-22 20:35', '2016-06-23 20:33', '2016-06-23 20:35', '2016-06-23 20:35', '2016-06-23 20:35', '2016-06-23 20:35',

In [199]:
len(sunset_time_local)

52726

In [200]:
accidents_data_hwy_westbound_sunset_df['Sunset_Date_Time_Local'] = sunset_time_local
accidents_data_hwy_westbound_sunset_df.head()

level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  Traffic_Signal  \
ID                                                        ...                   
A-12   One lane blocked due to accident on I-70 Westb...  ...           False   
A-85   Left lane blocked due to accident on I-76 West...  ...           False   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...           False   
A-143  Lane blocked due to accident on I-670 Westboun...  ...           False   
A-144  Left lane closed due to accident on I-70 Westb...  ...           False   

      Sunrise_Sunset Civil_Twilight Astronomical_Twilight   hwy  \
ID                                                                
A-12             Day            Day                   Day  True   
A-85             Day            Day                   Day  True   
A-100            Day            Day                   Day  True   
A-143          Night          Night                 Night  True   
A-144          Night          Night                   Day  True   

      Direction_West Accident_Date   Sunset_Time_UTC Accident_Time  \
ID                                                                   
A-12            True    2016-02-08  2016-02-08 22:59          8:21   
A-85            True    2016-02-10  2016-02-10 22:54         17:10   
A-100           True    2016-02-11  2016-02-11 23:08          8:13   
A-143           True    2016-02-15  2016-02-15 23:08          5:42   
A-144           True    2016-02-15  2016-02-15 23:08          6:36   

      Sunset_Date_Time_Local  
ID                            
A-12        2016-02-08 17:59  
A-85        2016-02-10 17:54  
A-100       2016-02-11 18:08  
A-143       2016-02-15 18:08  
A-144       2016-02-15 18:08  

[5 rows x 39 columns]

In [201]:
accidents_data_hwy_westbound_sunset_df['Sunset_Time_Local'] = accidents_data_hwy_westbound_sunset_df['Sunset_Date_Time_Local'].str.split(' ', n = 1, expand = True)[1]
accidents_data_hwy_westbound_sunset_df.head()

level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  Sunrise_Sunset  \
ID                                                        ...                   
A-12   One lane blocked due to accident on I-70 Westb...  ...             Day   
A-85   Left lane blocked due to accident on I-76 West...  ...             Day   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...             Day   
A-143  Lane blocked due to accident on I-670 Westboun...  ...           Night   
A-144  Left lane closed due to accident on I-70 Westb...  ...           Night   

      Civil_Twilight Astronomical_Twilight   hwy Direction_West Accident_Date  \
ID                                                                              
A-12             Day                   Day  True           True    2016-02-08   
A-85             Day                   Day  True           True    2016-02-10   
A-100            Day                   Day  True           True    2016-02-11   
A-143          Night                 Night  True           True    2016-02-15   
A-144          Night                   Day  True           True    2016-02-15   

        Sunset_Time_UTC Accident_Time Sunset_Date_Time_Local Sunset_Time_Local  
ID                                                                              
A-12   2016-02-08 22:59          8:21       2016-02-08 17:59             17:59  
A-85   2016-02-10 22:54         17:10       2016-02-10 17:54             17:54  
A-100  2016-02-11 23:08          8:13       2016-02-11 18:08             18:08  
A-143  2016-02-15 23:08          5:42       2016-02-15 18:08             18:08  
A-144  2016-02-15 23:08          6:36       2016-02-15 18:08             18:08  

[5 rows x 40 columns]

In [202]:
time_range_status = []

def time_in_range(startTime, endTime, accidentTime):
    if startTime < endTime:
        return startTime <= accidentTime and accidentTime <= endTime
    else: #Over midnight
        return accidentTime >= startTime or accidentTime <= endTime

for accident_time, sunset_time_local in zip(accidents_data_hwy_westbound_sunset_df.loc[:, 'Accident_Time'], accidents_data_hwy_westbound_sunset_df.loc[:, 'Sunset_Time_Local']):
    #print(accident_time, sunset_time_local)
    #print(str(int(sunset_time_local.split(':')[0]) + 1))
    start_time = str(int(sunset_time_local.split(':')[0]) - 1) + ':' + sunset_time_local.split(':')[1]
    start_time_no_seconds = datetime.strptime(start_time, '%H:%M').time()
    print(start_time_no_seconds)
    #end_time is same as sunset local time
    end_time = str(int(sunset_time_local.split(':')[0])) + ':' + sunset_time_local.split(':')[1]
    end_time_no_seconds = datetime.strptime(end_time, '%H:%M').time()
    print(end_time_no_seconds)
    accident_time_nosecs = accident_time.split(':')[0] + ':' + accident_time.split(':')[1]
    accident_time_no_seconds = datetime.strptime(accident_time_nosecs, '%H:%M').time()
    print(accident_time_no_seconds)
    print(time_in_range(start_time_no_seconds, end_time_no_seconds, accident_time_no_seconds))
    time_range_status.append(time_in_range(start_time_no_seconds, end_time_no_seconds, accident_time_no_seconds))
print(time_range_status)    

16:59:00
17:59:00
08:21:00
False
16:54:00
17:54:00
17:10:00
True
17:08:00
18:08:00
08:13:00
False
17:08:00
18:08:00
05:42:00
False
17:08:00
18:08:00
06:36:00
False
17:09:00
18:09:00
07:02:00
False
17:06:00
18:06:00
10:19:00
False
17:14:00
18:14:00
16:21:00
False
17:32:00
18:32:00
14:58:00
False
17:28:00
18:28:00
06:43:00
False
17:34:00
18:34:00
15:57:00
False
18:38:00
19:38:00
06:01:00
False
18:40:00
19:40:00
07:38:00
False
19:33:00
20:33:00
10:31:00
False
19:34:00
20:34:00
10:56:00
False
19:34:00
20:34:00
11:06:00
False
19:33:00
20:33:00
11:16:00
False
19:32:00
20:32:00
11:33:00
False
19:33:00
20:33:00
11:50:00
False
19:35:00
20:35:00
13:02:00
False
19:31:00
20:31:00
13:59:00
False
19:34:00
20:34:00
14:53:00
False
19:35:00
20:35:00
15:55:00
False
19:31:00
20:31:00
20:03:00
True
19:34:00
20:34:00
00:29:00
False
19:33:00
20:33:00
10:14:00
False
19:34:00
20:34:00
10:17:00
False
19:35:00
20:35:00
10:53:00
False
19:35:00
20:35:00
11:21:00
False
19:32:00
20:32:00
11:26:00
False
19:35:00
20:

16:48:00
14:53:00
False
15:50:00
16:50:00
15:37:00
False
15:47:00
16:47:00
16:38:00
True
15:50:00
16:50:00
07:24:00
False
15:51:00
16:51:00
08:20:00
False
15:50:00
16:50:00
11:21:00
False
15:50:00
16:50:00
11:57:00
False
15:50:00
16:50:00
12:29:00
False
15:50:00
16:50:00
12:32:00
False
15:51:00
16:51:00
15:19:00
False
15:49:00
16:49:00
20:04:00
False
15:48:00
16:48:00
01:21:00
False
15:48:00
16:48:00
10:21:00
False
15:50:00
16:50:00
13:31:00
False
15:50:00
16:50:00
14:13:00
False
15:51:00
16:51:00
15:06:00
False
15:44:00
16:44:00
18:39:00
False
15:51:00
16:51:00
21:29:00
False
15:51:00
16:51:00
03:14:00
False
15:51:00
16:51:00
07:11:00
False
15:50:00
16:50:00
08:31:00
False
15:50:00
16:50:00
09:04:00
False
15:49:00
16:49:00
09:07:00
False
15:51:00
16:51:00
11:49:00
False
15:45:00
16:45:00
12:22:00
False
15:51:00
16:51:00
20:50:00
False
15:51:00
16:51:00
21:22:00
False
15:51:00
16:51:00
21:37:00
False
15:50:00
16:50:00
22:16:00
False
15:51:00
16:51:00
02:18:00
False
15:52:00
16:52:00
07

18:17:00
19:01:00
False
17:20:00
18:20:00
00:54:00
False
17:19:00
18:19:00
06:36:00
False
17:18:00
18:18:00
09:28:00
False
17:20:00
18:20:00
14:55:00
False
17:16:00
18:16:00
16:35:00
False
17:15:00
18:15:00
17:36:00
True
17:16:00
18:16:00
17:33:00
True
17:19:00
18:19:00
05:51:00
False
17:17:00
18:17:00
07:39:00
False
17:18:00
18:18:00
08:42:00
False
17:18:00
18:18:00
08:49:00
False
17:17:00
18:17:00
09:35:00
False
17:19:00
18:19:00
09:43:00
False
17:19:00
18:19:00
09:52:00
False
17:17:00
18:17:00
10:21:00
False
17:17:00
18:17:00
10:30:00
False
17:14:00
18:14:00
11:43:00
False
17:17:00
18:17:00
11:58:00
False
17:18:00
18:18:00
12:15:00
False
17:17:00
18:17:00
12:25:00
False
17:15:00
18:15:00
12:26:00
False
17:19:00
18:19:00
17:44:00
True
17:19:00
18:19:00
21:26:00
False
17:19:00
18:19:00
22:14:00
False
17:15:00
18:15:00
01:09:00
False
17:17:00
18:17:00
05:46:00
False
17:15:00
18:15:00
06:31:00
False
17:17:00
18:17:00
08:13:00
False
17:17:00
18:17:00
08:50:00
False
17:15:00
18:15:00
08:5

15:51:00
False
18:19:00
19:19:00
16:18:00
False
18:17:00
19:17:00
22:09:00
False
18:16:00
19:16:00
08:45:00
False
18:19:00
19:19:00
08:53:00
False
18:17:00
19:17:00
09:04:00
False
18:18:00
19:18:00
09:45:00
False
18:15:00
19:15:00
09:50:00
False
18:19:00
19:19:00
10:50:00
False
18:19:00
19:19:00
11:23:00
False
18:19:00
19:19:00
11:38:00
False
18:15:00
19:15:00
11:48:00
False
18:16:00
19:16:00
11:55:00
False
18:19:00
19:19:00
12:20:00
False
18:19:00
19:19:00
12:50:00
False
18:19:00
19:19:00
13:02:00
False
18:17:00
19:17:00
16:11:00
False
18:19:00
19:19:00
18:38:00
True
18:17:00
19:17:00
20:37:00
False
18:17:00
19:17:00
20:52:00
False
18:14:00
19:14:00
21:58:00
False
18:18:00
19:18:00
22:15:00
False
18:17:00
19:17:00
01:13:00
False
18:17:00
19:17:00
02:46:00
False
18:17:00
19:17:00
03:16:00
False
18:17:00
19:17:00
04:55:00
False
18:17:00
19:17:00
05:07:00
False
18:15:00
19:15:00
07:13:00
False
18:15:00
19:15:00
09:02:00
False
18:17:00
19:17:00
09:07:00
False
18:14:00
19:14:00
09:52:00
Fa

False
17:23:00
18:23:00
16:46:00
False
19:15:00
20:15:00
18:29:00
False
19:17:00
20:17:00
20:49:00
False
19:16:00
20:16:00
01:25:00
False
19:16:00
20:16:00
03:24:00
False
19:16:00
20:16:00
03:51:00
False
19:16:00
20:16:00
03:53:00
False
19:16:00
20:16:00
09:37:00
False
19:13:00
20:13:00
10:04:00
False
19:13:00
20:13:00
09:59:00
False
19:14:00
20:14:00
10:18:00
False
19:14:00
20:14:00
11:49:00
False
19:16:00
20:16:00
12:43:00
False
19:16:00
20:16:00
12:59:00
False
19:16:00
20:16:00
14:18:00
False
19:16:00
20:16:00
18:11:00
False
19:16:00
20:16:00
22:57:00
False
19:15:00
20:15:00
06:40:00
False
19:15:00
20:15:00
07:03:00
False
19:15:00
20:15:00
12:39:00
False
19:15:00
20:15:00
13:57:00
False
19:12:00
20:12:00
10:36:00
False
19:13:00
20:13:00
10:46:00
False
19:14:00
20:14:00
11:26:00
False
19:11:00
20:11:00
17:22:00
False
19:14:00
20:14:00
18:18:00
False
19:11:00
20:11:00
23:11:00
False
19:11:00
20:11:00
23:14:00
False
19:10:00
20:10:00
10:41:00
False
19:10:00
20:10:00
11:24:00
False
19:1

...

18:58:00
19:58:00
16:21:00
False
18:59:00
19:59:00
18:53:00
False
19:38:00
20:38:00
10:32:00
False
19:05:00
20:05:00
11:04:00
False
19:05:00
20:05:00
12:55:00
False
19:07:00
20:07:00
06:02:00
False
18:58:00
19:58:00
09:58:00
False
18:57:00
19:57:00
11:48:00
False
18:58:00
19:58:00
13:18:00
False
19:26:00
20:26:00
04:53:00
False
19:27:00
20:27:00
17:55:00
False
19:26:00
20:26:00
10:31:00
False
20:01:00
21:01:00
10:09:00
False
19:53:00
20:53:00
15:21:00
False
19:35:00
20:35:00
22:51:00
False
19:34:00
20:34:00
23:08:00
False
19:33:00
20:33:00
04:34:00
False
19:34:00
20:34:00
04:58:00
False
19:35:00
20:35:00
05:37:00
False
19:35:00
20:35:00
06:03:00
False
19:34:00
20:34:00
06:53:00
False
19:34:00
20:34:00
07:15:00
False
19:35:00
20:35:00
07:46:00
False
19:32:00
20:32:00
09:25:00
False
19:34:00
20:34:00
10:17:00
False
19:34:00
20:34:00
10:58:00
False
19:33:00
20:33:00
11:30:00
False
19:14:00
20:14:00
09:47:00
False
19:21:00
20:21:00
09:52:00
False
19:07:00
20:07:00
01:22:00
False
19:03:00
2

10:50:00
False
19:04:00
20:04:00
14:46:00
False
19:03:00
20:03:00
16:38:00
False
18:59:00
19:59:00
17:36:00
False
18:59:00
19:59:00
18:05:00
False
19:53:00
20:53:00
16:09:00
False
19:54:00
20:54:00
22:50:00
False
19:17:00
20:17:00
10:41:00
False
20:09:00
21:09:00
01:09:00
False
20:09:00
21:09:00
01:48:00
False
20:11:00
21:11:00
09:15:00
False
20:11:00
21:11:00
09:15:00
False
20:14:00
21:14:00
09:17:00
False
19:26:00
20:26:00
07:22:00
False
19:23:00
20:23:00
17:03:00
False
19:39:00
20:39:00
05:39:00
False
19:34:00
20:34:00
17:25:00
False
20:22:00
21:22:00
16:31:00
False
19:27:00
20:27:00
09:01:00
False
19:29:00
20:29:00
09:09:00
False
19:29:00
20:29:00
17:05:00
False
19:18:00
20:18:00
18:06:00
False
19:49:00
20:49:00
18:25:00
False
20:13:00
21:13:00
06:59:00
False
20:07:00
21:07:00
16:41:00
False
19:24:00
20:24:00
16:36:00
False
20:06:00
21:06:00
18:29:00
False
19:49:00
20:49:00
08:42:00
False
19:54:00
20:54:00
17:42:00
False
19:33:00
20:33:00
13:11:00
False
19:32:00
20:32:00
15:19:00
F

19:02:00
20:02:00
08:06:00
False
19:29:00
20:29:00
11:26:00
False
19:06:00
20:06:00
06:53:00
False
18:58:00
19:58:00
15:25:00
False
19:11:00
20:11:00
19:22:00
True
19:59:00
20:59:00
18:16:00
False
19:26:00
20:26:00
03:58:00
False
19:28:00
20:28:00
06:47:00
False
19:29:00
20:29:00
07:43:00
False
19:28:00
20:28:00
07:56:00
False
19:29:00
20:29:00
08:06:00
False
19:29:00
20:29:00
08:21:00
False
19:29:00
20:29:00
08:29:00
False
19:27:00
20:27:00
08:59:00
False
19:27:00
20:27:00
09:02:00
False
19:29:00
20:29:00
10:55:00
False
19:27:00
20:27:00
12:00:00
False
19:28:00
20:28:00
12:25:00
False
19:27:00
20:27:00
13:31:00
False
19:28:00
20:28:00
16:31:00
False
19:27:00
20:27:00
16:42:00
False
19:27:00
20:27:00
17:22:00
False
19:28:00
20:28:00
18:43:00
False
19:04:00
20:04:00
22:50:00
False
19:02:00
20:02:00
23:01:00
False
18:59:00
19:59:00
04:36:00
False
19:02:00
20:02:00
05:09:00
False
19:02:00
20:02:00
07:43:00
False
19:02:00
20:02:00
07:51:00
False
18:57:00
19:57:00
08:35:00
False
18:59:00
19

False
19:31:00
20:31:00
04:34:00
False
19:59:00
20:59:00
15:30:00
False
19:34:00
20:34:00
15:17:00
False
19:19:00
20:19:00
04:16:00
False
19:19:00
20:19:00
06:35:00
False
19:19:00
20:19:00
07:41:00
False
19:17:00
20:17:00
07:56:00
False
19:19:00
20:19:00
08:46:00
False
19:17:00
20:17:00
11:53:00
False
19:19:00
20:19:00
15:20:00
False
19:25:00
20:25:00
06:17:00
False
19:27:00
20:27:00
08:45:00
False
19:28:00
20:28:00
14:27:00
False
19:29:00
20:29:00
14:37:00
False
19:35:00
20:35:00
15:19:00
False
19:27:00
20:27:00
16:00:00
False
19:27:00
20:27:00
17:19:00
False
19:34:00
20:34:00
17:34:00
False
19:59:00
20:59:00
06:38:00
False
19:12:00
20:12:00
10:33:00
False
19:59:00
20:59:00
17:38:00
False
19:14:00
20:14:00
17:12:00
False
19:52:00
20:52:00
07:44:00
False
19:40:00
20:40:00
08:18:00
False
19:39:00
20:39:00
13:08:00
False
19:25:00
20:25:00
07:41:00
False
19:25:00
20:25:00
07:42:00
False
19:25:00
20:25:00
08:57:00
False
19:17:00
20:17:00
09:04:00
False
19:25:00
20:25:00
12:03:00
False
19:2

19:55:00
08:37:00
False
18:48:00
19:48:00
08:42:00
False
18:58:00
19:58:00
09:38:00
False
18:53:00
19:53:00
10:30:00
False
18:56:00
19:56:00
12:37:00
False
18:48:00
19:48:00
12:47:00
False
18:54:00
19:54:00
12:54:00
False
18:53:00
19:53:00
15:40:00
False
18:56:00
19:56:00
16:45:00
False
18:55:00
19:55:00
18:15:00
False
18:52:00
19:52:00
20:43:00
False
19:46:00
20:46:00
12:00:00
False
19:46:00
20:46:00
16:04:00
False
19:46:00
20:46:00
16:55:00
False
19:46:00
20:46:00
19:34:00
False
20:03:00
21:03:00
08:19:00
False
20:03:00
21:03:00
08:38:00
False
19:18:00
20:18:00
17:33:00
False
19:25:00
20:25:00
16:34:00
False
20:01:00
21:01:00
05:37:00
False
19:38:00
20:38:00
07:02:00
False
19:42:00
20:42:00
20:23:00
True
19:23:00
20:23:00
07:33:00
False
19:18:00
20:18:00
07:37:00
False
19:22:00
20:22:00
10:55:00
False
19:20:00
20:20:00
15:28:00
False
19:22:00
20:22:00
15:35:00
False
19:25:00
20:25:00
15:37:00
False
19:20:00
20:20:00
16:18:00
False
19:23:00
20:23:00
17:09:00
False
19:21:00
20:21:00
22

In [203]:
accidents_data_hwy_westbound_sunset_df['Accidents_Close_To_Sunset_Status'] = time_range_status
accidents_data_hwy_westbound_sunset_df.head()

level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                    
A-12         1     11    OH         3    2/8/16 8:21    2/8/16 8:51   
A-85         5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-100        7     99    OH         2   2/11/16 8:13   2/11/16 8:43   
A-143       12    142    OH         3   2/15/16 5:42   2/15/16 6:12   
A-144       13    143    OH         3   2/15/16 6:36   2/15/16 9:00   

       Start_Lat  Start_Lng  Distance(mi)  \
ID                                          
A-12   39.932709 -82.830910          0.01   
A-85   41.040714 -81.613144          0.01   
A-100  39.749916 -84.139359          0.01   
A-143  39.975986 -82.996307          0.71   
A-144  39.951401 -83.040161          0.01   

                                             Description  ...  Civil_Twilight  \
ID                                                        ...                   
A-12   One lane blocked due to accident on I-70 Westb...  ...             Day   
A-85   Left lane blocked due to accident on I-76 West...  ...             Day   
A-100  Accident on US-35 Westbound at Smithville Rd. ...  ...             Day   
A-143  Lane blocked due to accident on I-670 Westboun...  ...           Night   
A-144  Left lane closed due to accident on I-70 Westb...  ...           Night   

      Astronomical_Twilight   hwy Direction_West Accident_Date  \
ID                                                               
A-12                    Day  True           True    2016-02-08   
A-85                    Day  True           True    2016-02-10   
A-100                   Day  True           True    2016-02-11   
A-143                 Night  True           True    2016-02-15   
A-144                   Day  True           True    2016-02-15   

        Sunset_Time_UTC Accident_Time Sunset_Date_Time_Local  \
ID                                                             
A-12   2016-02-08 22:59          8:21       2016-02-08 17:59   
A-85   2016-02-10 22:54         17:10       2016-02-10 17:54   
A-100  2016-02-11 23:08          8:13       2016-02-11 18:08   
A-143  2016-02-15 23:08          5:42       2016-02-15 18:08   
A-144  2016-02-15 23:08          6:36       2016-02-15 18:08   

      Sunset_Time_Local Accidents_Close_To_Sunset_Status  
ID                                                        
A-12              17:59                            False  
A-85              17:54                             True  
A-100             18:08                            False  
A-143             18:08                            False  
A-144             18:08                            False  

[5 rows x 41 columns]

In [204]:
accidents_data_hwy_westbound_close_to_sunset_df = accidents_data_hwy_westbound_sunset_df.loc[accidents_data_hwy_westbound_sunset_df['Accidents_Close_To_Sunset_Status'] == True]
accidents_data_hwy_westbound_close_to_sunset_df.head()


level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                     
A-85          5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-811        68    810    CA         3  6/21/16 20:03  6/21/16 20:48   
A-1176      144   1175    CA         3  6/24/16 19:57  6/24/16 20:27   
A-1177      145   1176    CA         3  6/24/16 20:07  6/24/16 21:07   
A-1591      238   1590    CA         3  6/28/16 20:04  6/28/16 21:04   

        Start_Lat   Start_Lng  Distance(mi)  \
ID                                            
A-85    41.040714  -81.613144          0.01   
A-811   37.766987 -121.335495          0.00   
A-1176  37.701668 -121.769699          0.00   
A-1177  38.710537 -121.306374          0.00   
A-1591  38.758034 -121.261528          0.00   

                                              Description  ...  \
ID                                                         ...   
A-85    Left lane blocked due to accident on I-76 West...  ...   
A-811   Two lanes blocked due to accident on I-205 Wes...  ...   
A-1176  Lane blocked due to accident on I-580 Westboun...  ...   
A-1177  Accident on I-80 Westbound at Exit 100 Antelop...  ...   
A-1591  Right hand shoulder blocked due to accident on...  ...   

        Civil_Twilight Astronomical_Twilight   hwy Direction_West  \
ID                                                                  
A-85               Day                   Day  True           True   
A-811              Day                   Day  True           True   
A-1176             Day                   Day  True           True   
A-1177             Day                   Day  True           True   
A-1591             Day                   Day  True           True   

       Accident_Date   Sunset_Time_UTC Accident_Time Sunset_Date_Time_Local  \
ID                                                                            
A-85      2016-02-10  2016-02-10 22:54         17:10       2016-02-10 17:54   
A-811     2016-06-21  2016-06-21 03:31         20:03       2016-06-20 20:31   
A-1176    2016-06-24  2016-06-24 03:32         19:57       2016-06-23 20:32   
A-1177    2016-06-24  2016-06-24 03:34         20:07       2016-06-23 20:34   
A-1591    2016-06-28  2016-06-28 03:34         20:04       2016-06-27 20:34   

       Sunset_Time_Local Accidents_Close_To_Sunset_Status  
ID                                                         
A-85               17:54                             True  
A-811              20:31                             True  
A-1176             20:32                             True  
A-1177             20:34                             True  
A-1591             20:34                             True  

[5 rows x 41 columns]

In [205]:
len(accidents_data_hwy_westbound_close_to_sunset_df)

2565

In [206]:
accidents_data_hwy_westbound_close_to_sunset_df['accident_time_sunset_time'] = list(zip(accidents_data_hwy_westbound_close_to_sunset_df.Accident_Time, accidents_data_hwy_westbound_close_to_sunset_df.Sunset_Time_Local))
accidents_data_hwy_westbound_close_to_sunset_df.head()

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


level_0  index State  Severity     Start_Time       End_Time  \
ID                                                                     
A-85          5     84    OH         3  2/10/16 17:10  2/10/16 23:59   
A-811        68    810    CA         3  6/21/16 20:03  6/21/16 20:48   
A-1176      144   1175    CA         3  6/24/16 19:57  6/24/16 20:27   
A-1177      145   1176    CA         3  6/24/16 20:07  6/24/16 21:07   
A-1591      238   1590    CA         3  6/28/16 20:04  6/28/16 21:04   

        Start_Lat   Start_Lng  Distance(mi)  \
ID                                            
A-85    41.040714  -81.613144          0.01   
A-811   37.766987 -121.335495          0.00   
A-1176  37.701668 -121.769699          0.00   
A-1177  38.710537 -121.306374          0.00   
A-1591  38.758034 -121.261528          0.00   

                                              Description  ...  \
ID                                                         ...   
A-85    Left lane blocked due to accident on I-76 West...  ...   
A-811   Two lanes blocked due to accident on I-205 Wes...  ...   
A-1176  Lane blocked due to accident on I-580 Westboun...  ...   
A-1177  Accident on I-80 Westbound at Exit 100 Antelop...  ...   
A-1591  Right hand shoulder blocked due to accident on...  ...   

        Astronomical_Twilight   hwy Direction_West Accident_Date  \
ID                                                                 
A-85                      Day  True           True    2016-02-10   
A-811                     Day  True           True    2016-06-21   
A-1176                    Day  True           True    2016-06-24   
A-1177                    Day  True           True    2016-06-24   
A-1591                    Day  True           True    2016-06-28   

         Sunset_Time_UTC Accident_Time Sunset_Date_Time_Local  \
ID                                                              
A-85    2016-02-10 22:54         17:10       2016-02-10 17:54   
A-811   2016-06-21 03:31         20:03       2016-06-20 20:31   
A-1176  2016-06-24 03:32         19:57       2016-06-23 20:32   
A-1177  2016-06-24 03:34         20:07       2016-06-23 20:34   
A-1591  2016-06-28 03:34         20:04       2016-06-27 20:34   

       Sunset_Time_Local Accidents_Close_To_Sunset_Status  \
ID                                                          
A-85               17:54                             True   
A-811              20:31                             True   
A-1176             20:32                             True   
A-1177             20:34                             True   
A-1591             20:34                             True   

       accident_time_sunset_time  
ID                                
A-85              (17:10, 17:54)  
A-811             (20:03, 20:31)  
A-1176            (19:57, 20:32)  
A-1177            (20:07, 20:34)  
A-1591            (20:04, 20:34)  

[5 rows x 42 columns]

In [207]:
percentage_accident_close_to_sunset = len(accidents_data_hwy_westbound_close_to_sunset_df)/len(accidents_data_hwy_westbound_df) * 100
print(percentage_accident_close_to_sunset)

4.864772597959261
